In [1]:
from os import listdir
from os.path import isfile, join
import re
import csv
import gensim
import numpy as np
from gensim.models.word2vec import Word2Vec
from gensim.models import KeyedVectors
from gensim.models.wrappers import FastText
import logging
import os
import pandas as pd 
import sys
import sklearn.metrics
import sklearn
import matplotlib.pyplot as plt #For graphics
import seaborn #Makes the graphics look nicer
import random
import math
import warnings
import utils
from utils import *
from utils2 import *
import scipy.stats
from dataDictionariesLexicons import *
from testData import *
from polesConstructs import *

random.seed(1)

warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.simplefilter(action='ignore', category=DeprecationWarning)
# warnings.filterwarnings('ignore')

sys.path.insert(0, '../') # necessary in order to import word2vecTraining where the epoch saver class, which is part of the model, is located

In [2]:
modelsPath = os.path.normpath(r'D:\data\wordVectors') 
# modelFilePath = os.path.join(modelsPath, 'GoogleNews-vectors-negative300.bin')
# model2 = KeyedVectors.load_word2vec_format(modelFilePath,binary=True) 
modelFilePath = os.path.join(modelsPath, 'GoogleNews-vectors-negative300LowerCase.bin')
model1 = KeyedVectors.load(modelFilePath) 

In [3]:
modelsPath = os.path.normpath(r'D:\data\wordVectors') 
modelFilePath = os.path.join(modelsPath, 'glove.6B.300d.txt.word2vec.bin')
model2 = KeyedVectors.load_word2vec_format(modelFilePath,binary=True) 

In [4]:
modelsPath = os.path.normpath(r'D:\data\wordVectors') 
modelFilePath = os.path.join(modelsPath, 'glove.twitter.27B.200d.txt.word2vec.bin')
model3 = KeyedVectors.load(modelFilePath) 

In [5]:
modelsPath = os.path.normpath(r'D:\data\wordVectors') 
modelFilePath = os.path.join(modelsPath, 'glove.42B.300d.txt.word2vec.bin')
model4 = KeyedVectors.load(modelFilePath) 

In [6]:
modelsPath = os.path.normpath(r'D:\data\wordVectors') 
modelFilePath = os.path.join(modelsPath, 'glove.840B.300d.txt.word2vec.bin')
model5 = KeyedVectors.load(modelFilePath) 

In [7]:
modelsPath = os.path.normpath(r'D:\data\wordVectors') 
modelFilePath = os.path.join(modelsPath, 'fastext-common-crawl-300d-2M-subword.bin')
model6 = KeyedVectors.load(modelFilePath)

In [8]:
modelsPath = os.path.normpath(r'D:\data\wordVectors') 
modelFilePath = os.path.join(modelsPath, 'fastext-wiki-news-300d-1M-subword-Original.bin')
model7 = KeyedVectors.load(modelFilePath)

In [9]:
# models = [model1,model2,model3,model4]
# models = [model1,model2]
models = [model1,model2,model3,model4,model5,model6,model7]
# models = [model1]

In [10]:
#change default lexicons
# lexicons = [harvardGeneralInquirer3623, vaderLexicon7062,NRCEmotionLexicon5555,opinionLexicon6786,afinnLexicon2477]
# lexicons = [WEAT1]
lexicons = [harvardGeneralInquirer3623]
dataDict = dataDictLoadLexicons(dataDict,lexicons)
# WEAT1 harvardGeneralInquirer3623

In [11]:
dataSetIndexes = [
# '0-1', #percentage females per occupation
# '0-2', #country's GDP per capita
# '0-3', #car brands and prices
# '0-4', #voting behavior by ethnic/racial group
# '0-5', #voting behavior by profession
    
'1-1', #gender
'1-2',
'1-3',
'1-4',
'1-5',
    
'2-1', #Race/ethnicity
'2-2',
'2-3',
'2-4',    
  
'3-1', #Sexual orientation  
    
'4-1', #religiosity    
'4-2', #religion Islam and Christianity
    
'5-1', #age 
'6-1', #socioeconomic status
'7-1', #physical beauty
    
'8-1', #Personal ideology
'8-2', #Party affiliation and political parties
'8-3', #US presidents
'8-4', #Ideologies abstract
'8-5', #influential conservatives and liberals
]

In [12]:
rows = len(dataSetIndexes)
columns = len(models)
outputMatrix = np.zeros((rows,columns))
outputMatrixPvalues = np.zeros((rows,columns))

## Dimensions against models

In [13]:
#Checking for the existence of uppercase letters in models
# [w for w in model6.wv.vocab if any(x.isupper() for x in w)]

In [14]:
#Checking for the existence _ in models
# [w for w in model2.wv.vocab if '-' in w]

In [15]:
random.seed(0)
outputMatrices = []
for outputMatrixIndex in range(500):
    print("outputMatrixIndex",outputMatrixIndex)
    for rowNumber, dataSetIndex in enumerate(dataSetIndexes):
        print(dataDict[dataSetIndex]['name'])
        modelsCorrelations=[]
        modelspvalues=[]
        for i,model in enumerate(models):    
    #         print("model", i+1)
            correlations = []
            pvalues = []
            constructPole1 = dataDict[dataSetIndex]['constructPole1']
            constructPole2 = dataDict[dataSetIndex]['constructPole2']

            lengthPole1 = len(constructPole1)
            lengthPole2 = len(constructPole2)
            chunkSize=1
            if len(constructPole1) > 2:
                constructPole1 = random.sample(constructPole1,k=chunkSize*(max(1,round(lengthPole1/4))))
            else:
                if chunkSize <= 2:
                    constructPole1 = random.sample(constructPole1,k=1)
            if len(constructPole2) > 2:
                constructPole2 = random.sample(constructPole2,k=chunkSize*(max(1,round(lengthPole2/4))))
            else:
                if chunkSize <= 2:
                    constructPole2 = random.sample(constructPole2,k=1)

            if i>=1: #Glove and fastext vocabulary uses - instead of _ So we need to alter Construct poles and real data - Checked!
                constructPole1,constructPole2,RealDataTemp=replaceUnderscoreForDash(constructPole1,constructPole2,RealDataTemp)
            if i in [1,2,3]: # Lowercase poles for models With only lowercase vocabularies - Checked!
                constructPole1 = list(set(list(map(str.lower,constructPole1))))
                constructPole2 = list(set(list(map(str.lower,constructPole2))))
            constructPole1,constructPole2 = constructsFilter(model,constructPole1,constructPole2,printFlag=False)# Filter out terms not in model vocabulary

            for RealDataTemp in dataDict[dataSetIndex]['RealDataLexicons']:
    #         for RealDataTemp in [voteByEthnicity]:
                RealData = realDataFilter(model,RealDataTemp,0)#Filter out terms not in model vocabulary (Last parameter Flag prints out OOV words)
                Axis = dimensionN(model, constructPole1,constructPole2)  
                AxisName='Axis'
                try:
                    dataFrame = makeDF(model, RealData.keys(),Axis,AxisName)
                except:
                    continue
                dataFrame['RealValues']=RealData.values()
                spearmanCorr,pearsonCorr=calculateCorrelations(dataFrame,printFlag=False)
    #             correlations.append(pearsonCorr[0])
    #             pvalues.append(pearsonCorr[1])
                correlations.append(spearmanCorr[0])
                pvalues.append(spearmanCorr[1])            
    #         print("correlations for model", i+1)
    #         print(*correlations)
    #         print("mean: ", np.array(correlations).mean())
#             modelsCorrelations.append(np.array(correlations).mean())
            modelsCorrelations.append(np.nanmean(correlations))
#             modelspvalues.append(np.array(pvalues).mean())#This can only be done if only one lexicon is being tested
            modelspvalues.append(np.nanmean(pvalues))#This can only be done if only one lexicon is being tested
    #         print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
        print(*modelsCorrelations)
        print(np.array(modelsCorrelations).mean())
        outputMatrix[rowNumber]=modelsCorrelations
        outputMatrixPvalues[rowNumber]=modelspvalues
        #Print closest neighbors to axis Poles
    #     print([w[0] for w in model.wv.similar_by_vector(-Axis,restrict_vocab=50000,topn=50)])
    #     print([w[0] for w in model.wv.similar_by_vector(Axis,restrict_vocab=50000,topn=50)])

        print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
    outputMatrices.append(outputMatrix)
# outputMatrix=np.array(outputMatrices).mean(axis=0) #shape of outputMatrices=(2,20,7)    
outputMatrix=np.nanmean(np.array(outputMatrices),axis=0) #shape of outputMatrices=(2,20,7)    

outputMatrixIndex 0
gender general
0.28657679500248223 0.0883874118176092 -0.006864942114527506 0.01789381226081634 0.15994988267884724 -0.024394880684639443 -0.007350836980330976
0.07345674885432243
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
gender family roles
0.161556015324207 0.2166914063886125 -0.11647309035697796 -0.06227127854175317 0.0843451742255464 0.11631884192564114 0.11717010631688847
0.07390531075459492
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
gender and young age
0.18145861380123005 0.0895194092047702 0.13809349795979742 0.19483002422889317 0.156796392705776 0.1903600394281935 0.11702840472383809
0.15258376886464262
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
gender masculinity and femininity
0.2557289726072513 0.2026919319882181 0.03392964670714463 0.3003437476774679 0.279058758614648 0.08566221793482993 0.12807417758286233
0.18364135044463176
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
gender and popular given names 
-0.02541752789756377

C:\Users\drozado\Sync\workspace\AlgorithmicBias\AlgorithmicBiasInWordEmbeddings\analysis\utils.py:15: RuntimeWarning: invalid value encountered in double_scalars
  normalized_vector = vector / np.linalg.norm(vector)
C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:66: RuntimeWarning: Mean of empty slice
C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:68: RuntimeWarning: Mean of empty slice
C:\Users\drozado\Sync\workspace\AlgorithmicBias\AlgorithmicBiasInWordEmbeddings\analysis\utils.py:15: RuntimeWarning: invalid value encountered in double_scalars
  normalized_vector = vector / np.linalg.norm(vector)
C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:66: RuntimeWarning: Mean of empty slice
C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:68: RuntimeWarning: Mean of empty slice
C:\Users\drozado\Sync\workspace\AlgorithmicBias\AlgorithmicBiasInWordEmbeddings\analysis\utils.py:15: RuntimeWarning: invalid value enco

-0.038752884890848355 nan nan -0.03444856636402943 -0.005131898994444268 0.08341873132569087 nan
nan
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
Whites and Asians


C:\Users\drozado\Sync\workspace\AlgorithmicBias\AlgorithmicBiasInWordEmbeddings\analysis\utils.py:15: RuntimeWarning: invalid value encountered in double_scalars
  normalized_vector = vector / np.linalg.norm(vector)
C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:66: RuntimeWarning: Mean of empty slice
C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:68: RuntimeWarning: Mean of empty slice


0.1710533392643932 -0.16901440360714842 0.05300874092121936 -0.05941209293439369 -0.15944406374177092 0.1660124040892718 nan
nan
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
sexual orientation
-0.06700862885705716 0.08711825979040053 0.038589475911940896 0.1517125652148169 -0.04635587530198288 -0.17684146440434867 -0.01487064642539883
-0.0039509020102327435
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
religiosity
-0.15246151076377376 -0.1806108423739324 -0.08189594643007297 -0.1861744847618167 -0.05471497389252573 0.12129695321171916 -0.04086139220579924
-0.08220317103088594
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
religion Christianity and Islam
-0.12494016223591775 -0.37104292744164447 -0.19163144333947474 -0.22882191140474917 -0.4476850117410848 -0.22512620772787637 -0.3485811063969676
-0.2768326814696736
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
age
0.06487829285535832 -0.02629381206263774 0.18220368006189777 0.21185481071291634 -0.15694434608019006 0

...

C:\Users\drozado\Sync\workspace\AlgorithmicBias\AlgorithmicBiasInWordEmbeddings\analysis\utils.py:15: RuntimeWarning: invalid value encountered in double_scalars
  normalized_vector = vector / np.linalg.norm(vector)
C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:66: RuntimeWarning: Mean of empty slice
C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:68: RuntimeWarning: Mean of empty slice
C:\Users\drozado\Sync\workspace\AlgorithmicBias\AlgorithmicBiasInWordEmbeddings\analysis\utils.py:15: RuntimeWarning: invalid value encountered in double_scalars
  normalized_vector = vector / np.linalg.norm(vector)
C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:66: RuntimeWarning: Mean of empty slice
C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:68: RuntimeWarning: Mean of empty slice
C:\Users\drozado\Sync\workspace\AlgorithmicBias\AlgorithmicBiasInWordEmbeddings\analysis\utils.py:15: RuntimeWarning: invalid value enco

nan nan -0.018007667434727273 -0.032610098801815465 0.2323540979209958 0.04096278242870704 nan
nan
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
U.S. presidents
0.046362528652511364 -0.04246458731886868 0.20021474345981183 0.001706538018963858 0.14015404165886647 0.26243027855345896 0.179617731024152
0.11257446772127085
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
ideologies abstract


C:\Users\drozado\Sync\workspace\AlgorithmicBias\AlgorithmicBiasInWordEmbeddings\analysis\utils.py:15: RuntimeWarning: invalid value encountered in double_scalars
  normalized_vector = vector / np.linalg.norm(vector)
C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:66: RuntimeWarning: Mean of empty slice
C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:68: RuntimeWarning: Mean of empty slice
C:\Users\drozado\Sync\workspace\AlgorithmicBias\AlgorithmicBiasInWordEmbeddings\analysis\utils.py:15: RuntimeWarning: invalid value encountered in double_scalars
  normalized_vector = vector / np.linalg.norm(vector)
C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:66: RuntimeWarning: Mean of empty slice
C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:68: RuntimeWarning: Mean of empty slice
C:\Users\drozado\Sync\workspace\AlgorithmicBias\AlgorithmicBiasInWordEmbeddings\analysis\utils.py:15: RuntimeWarning: invalid value enco

nan nan nan 0.007639628571280144 -0.12207862597819169 0.22770735175663637 -0.12306248634217075
nan
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
influential conservatives and liberals
0.12105981172138257 0.16815536821136456 0.10020528870457249 0.21540462344344335 0.15897162779641508 -0.04669148078912558 0.1876348328413835
0.12924858170420514
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX


C:\Users\drozado\miniconda3\lib\site-packages\ipykernel_launcher.py:81: RuntimeWarning: Mean of empty slice


In [26]:
#print output matrix
for r in outputMatrix:
    print(*r)

0.08622664865412787 0.1519436351827043 -0.1401480564455759 0.14104336428846567 0.12722735000313848 0.37546730395029226 -0.056775817912836396
-0.06394677303967895 0.14604787162531233 -0.02272862399817836 -0.005956058043651371 0.28551476019061783 0.21793156903592287 0.0802410669989861
0.18145861380122977 -0.04130321890331246 -0.029869205227962443 0.003275271089917525 0.2373813078848428 0.1640985672034192 0.14542326507915995
0.16366117511466996 0.23645945966975693 0.1309523507380187 0.2886484874569787 -0.04434221385237563 0.03666692596553599 0.10533187399621317
-0.019525223140538877 -0.10916216404557845 -0.01743657941359877 -0.05066414937427141 -0.00011376920126425646 0.22002531192750144 0.006478169055868708
-0.1718905822039584 0.22034634864576116 -0.10647876701211145 -0.1579250045474239 nan nan 0.11188918204154612
-0.08594060404137659 -0.14720331194222658 -0.06000669164247513 -0.16568534598014106 -0.2166982807460835 0.01448350115248682 -0.13332836570857126
0.046253253182471796 nan 0.0979

In [17]:
#print P values output matrix
for r in outputMatrixPvalues:
    print(*r)

2.151200275784711e-07 5.172955743238059e-20 7.56989697932077e-17 1.663251892584128e-17 1.6690919956779372e-14 2.677281137326499e-121 0.0006439929934270065
0.00012173573636512007 1.3564205235486717e-18 0.17840525705627505 0.7205017498165773 1.0632901030718293e-68 4.350640781042644e-40 1.3888893243119417e-06
4.556909803587915e-28 0.013261550446225278 0.07695794070156653 0.844024232533859 1.9598501985905527e-47 3.2005034648301195e-23 1.6350406599401654e-18
4.545311518231041e-23 7.201694393388245e-47 6.928865647344581e-15 3.056524929964873e-70 0.007699228921716207 0.027548443961496416 2.2494251715739277e-10
0.24111898547347113 5.2904912561194894e-11 0.3019300268542979 0.002323777198751205 0.9945471349695747 7.575803689723249e-41 0.6972428806575413
2.58799620378931e-25 8.852671678899578e-41 2.592129243556138e-10 1.3396518863288034e-21 nan nan 1.5775171736714192e-11
2.3597209190765258e-07 7.225785300745591e-19 0.00037721883934977563 1.217719185103273e-23 1.2374020422948044e-39 0.384190259107

## adjusting P values for multiple tests

In [18]:
outputMatrixPvalues.shape

(20, 7)

In [19]:
from rpy2.robjects.packages import importr
from rpy2.robjects.vectors import FloatVector

stats = importr('stats')

#bonferroni most conservative, holm also valid under arbitrary assumptions
p_adjust = stats.p_adjust(FloatVector(outputMatrixPvalues.flatten()), method = 'holm')
outputMatrixPvaluesCorrected = np.array(p_adjust).reshape(outputMatrixPvalues.shape)

In [20]:
#print P values output matrix
for r in outputMatrixPvaluesCorrected:
    print(*r)

8.819921130717315e-06 3.931446364860925e-18 5.223228915731331e-15 1.1809088437347307e-15 1.0849097971906591e-12 3.319828610284859e-119 0.0199637827962372
0.004139015036414082 9.901869821905303e-17 1.0 1.0 1.233416519563322e-66 4.3941471888530704e-38 5.277779432385378e-05
4.237926117336761e-26 0.2917541098169561 1.0 1.0 2.1362367164637024e-45 2.7204279451056016e-21 1.177229275156919e-16
3.818061675314074e-21 7.777829944859305e-45 4.573051327247423e-13 3.576134168058901e-68 0.18478149412118897 0.5509688792299283 1.1247125857869638e-08
1.0 2.6981505406209394e-09 1.0 0.06971331596253616 1.0 7.878835837312179e-39 1.0
2.303316621372486e-23 9.02972511247757e-39 1.2701433293425077e-08 1.0717215090630427e-19 nan nan 8.360841020458522e-10
9.438883676306103e-06 5.3470811225517374e-17 0.01207100285919282 1.0472384991888148e-21 1.2374020422948045e-37 1.0 5.968451138652861e-14
0.14354124640168564 nan 2.796645551932032e-07 1.8263018225720584e-08 4.5531713200836637e-10 0.14354124640168564 1.1722603631